In [10]:
# Configure LLM options
#from langchain_community.chat_models import ChatOllama
from langchain_ollama import ChatOllama
from langchain_community.llms import DeepInfra
import os
from dotenv import load_dotenv
from langchain_community.utilities import SQLDatabase

load_dotenv()

api = os.getenv("DEEPINFRA_API_KEY")
# API setup (optional)
deepinfra_model = "meta-llama/Llama-3.3-70B-Instruct"
# "https://api.python.langchain.com/en/latest/llms/langchain_community.llms.deepinfra.DeepInfra.html"

di = DeepInfra(model_id=deepinfra_model,
                    deepinfra_api_token=api)

# Choose which model to use
llm = di 

# Initialize database connection
db = SQLDatabase.from_uri("sqlite:///Spring_2025_courses.db", sample_rows_in_table_info=0)

# Helper functions
def get_schema(_):
    """Retrieve database schema"""
    return db.get_table_info()

def run_query(query):
    """Execute SQL query"""
    return db.run(query)

# print(get_schema(_))

In [11]:
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough

# SQL generation prompt
system_prompt = """ 
You are a SQLite expert. Given an input question, create one syntactically correct SQLite query to run. Generate only one query. No pre-amble.

Here is the relevant table information:
schema: {schema}
Departments: 'Applied Math & Statistics', 'ART', 'Biomedical Science (BMS)', 'Computer Science (CS), Computer Networks and Cybersecurity (CNCS)', 'Data Science (DS)', 'Dance', 'General Education (GE)'
New/Repeat: Have no values 

Tips:
- Use LIKE instead of = in the queries
- Don't use New/Repeat in queries

Below are a number of examples of questions and their corresponding SQL queries.

example 1:
Question:List all departments.
SQL query:SELECT Department FROM Spring_2025_courses;

example 2:
Question:Find all classes that are taught by Dr. Qu.
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Instructor LIKE '%Qu%';

example 3:
Question:List all courses in the Data Science department.
SQL query:SELECT CourseCode, CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Data Science%';

example 4:
Question:Find the total number of courses offered for Spring 2025.
SQL query:SELECT COUNT(CourseCode) FROM Spring_2025_courses;

example 5:
Question:List all professors from Biomed Department.
SQL query:SELECT Instructor FROM Spring_2025_courses WHERE Department LIKE '%Biomed%';

example 6:
Question:Which courses are available in the Biomed department for Spring 2025?
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Biomed%';

example 7:
Question:How many courses are offered under the Arts Management (BFA) program?
SQL query:SELECT COUNT(CourseCode) FROM Spring_2025_courses WHERE Department LIKE Program LIKE '%BFA%'

example 8:
Question:Which courses are available for the Master of Science in Applied Math?
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Program LIKE '%Master of Science%' AND Department LIKE '%Applied Math%';

Write only one SQLite query that would answer the user's question. No pre-amble.
"""

human_prompt = """Based on the table schema below, write a SQL query that would answer the user's question:
{schema}

Question: {question}
SQL Query:"""

prompt = ChatPromptTemplate.from_messages([
    ("system", system_prompt),
    ("human", human_prompt),
])

# Build query generation chain
sql_generator = (
    RunnablePassthrough.assign(schema=get_schema)
    | prompt
    | llm.bind(stop=["\nSQLResult:"])
    | StrOutputParser()
)

# Natural language response generation
nl_system_prompt = """Given an input question and SQL response, convert it to a natural language answer. 

Below are a number of examples of questions and their corresponding SQL queries.

example 1: 
Question: Which courses are available in the Data Science department?
SQL Query: SELECT CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Data Science%';
SQL Response: [('Introduction to Data Science',), ('Career Development in Data Science',), ('Data Structures',), ('Data Visualization',), ('Data Inference',), ('Data Mining',), ('Big Data Engineering',), ('Independent Study for Data Science',), ('Senior Project',), ('Mathematical Foundation for Data Science (Online)',), ('Computational Foundation for Data Science (Online)',), ('Probability for Data Science (Online)',), ('Exploratory Data Analysis and Visualization',), ('Modern Applied Statistical Learning',), ('Data Mining for Business',), ('Big Data and Data Engineering',), ('Design and Analysis of Experiments',), ('Design and Analysis of Experiments',), ('Computer Vision and Natural Language Processing (Independent Study)',), ('Capstone Project',)]
Response: The available courses in the Data Science department are Introduction to Data Science, Career Development in Data Science, Data Structures, Data Visualization, Data Inference, Data Mining, Big Data Engineering, Independent Study for Data Science, Senior Project, Mathematical Foundation for Data Science, Computational Foundation for Data Science, Probability for Data Science, Exploratory Data Analysis and Visualization, Modern Applied Statistical Learning, Data Mining for Business, Big Data and Data Engineering, Design and Analysis of Experiments, and Capstone Project.

example 2:
Question: Find all classes that are taught by Dr. Qu.
SQL Query: SELECT CourseTitle FROM Spring_2025_courses WHERE Instructor LIKE '%Qu%';
SQL Response: [('Introduction to Data Science',), ('Data Structures',), ('Data Mining',), ('Computational Foundation for Data Science (Online)',), ('Data Mining for Business',), ('Computer Vision and Natural Language Processing (Independent Study)',)]
Response:  Dr. Qu is teaching Introduction to Data Science, Data Structures, Data Mining, Computational Foundation for Data Science, Data Mining for Business, and Computer Vision and Natural Language Processing.

Generate only ONE answer based on the SQL response. No pre-amble.
"""

response_prompt = """Based on the table schema below, question, sql query, and sql response, write a natural language response:
{schema}

Question:{question}
SQL Query:{query}
SQL Response:{response}
Response:"""

nl_prompt = ChatPromptTemplate.from_messages([
    ("system", nl_system_prompt),
    ("human", response_prompt),
])

# Complete chain with natural language output
complete_chain = (
    RunnablePassthrough.assign(query=sql_generator)
    | RunnablePassthrough.assign(
        schema=get_schema,
        response=lambda x: db.run(x['query']),
    )
    | nl_prompt
    | llm
)

In [ ]:
def demonstrate_chain_steps(question: str):
    """
    Demonstrate each step of the complete chain
    
    Args:
        question (str): Natural language question
    """
    print("\n=== Chain Demonstration ===\n")
    
    # Step 1: Initial input
    print("1. Initial Input:")
    print({"question": question})
    
    # Step 2: Generate SQL
    sql = sql_generator.invoke({"question": question})
    print("\n2. Generated SQL:")
    print(sql)
    
    # Step 3: Execute SQL
    db_result = db.run(sql)
    print("\n3. Database Result:")
    print(db_result)
    
    # Step 4: Get schema
    schema = get_schema(None)
    print("\n4. Database Schema:")
    print(schema[:200] + "...")  # Truncated for readability
    
    # Step 5: Complete response
    final_response = complete_chain.invoke({"question": question})
    print("\n5. Final Natural Language Response:")
    print(final_response)
    
    print("\n=== End Demonstration ===\n")

# Example usage
demonstrate_chain_steps("Find all classes that are taught by Dr. Bess.")

In [42]:
from langchain.memory import ConversationBufferMemory
from langchain_core.prompts import MessagesPlaceholder
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough

# SQL generation prompt
system_prompt = """ 
You are a SQLite expert. Given an input question, create one syntactically correct SQLite query to run. Generate only one query. No preamble.

Here is the relevant table information:
schema: {schema}
Departments: 'Applied Math & Statistics', 'ART', 'Biomedical Science (BMS)', 'Computer Science (CS), Computer Networks and Cybersecurity (CNCS)', 'Data Science (DS)', 'Dance', 'General Education (GE)'
New/Repeat: Have no values (Don't use New/Repeat in queries)

Tips:
- Use LIKE instead of = in the queries

Below are a number of examples of questions and their corresponding SQL queries.

example 1:
Question: List all departments.
SQL query: SELECT Department FROM Spring_2025_courses;

example 2:
Question: Find all classes that are taught by Dr. Qu.
SQL query: SELECT CourseTitle FROM Spring_2025_courses WHERE Instructor LIKE '%Qu%';

example 3:
Question: List all courses in the Data Science department.
SQL query: SELECT CourseCode, CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Data Science%';

example 4:
Question: Find the total number of courses offered for Spring 2025.
SQL query: SELECT COUNT(CourseCode) FROM Spring_2025_courses;

example 5:
Question: List all professors from Biomed Department.
SQL query: SELECT Instructor FROM Spring_2025_courses WHERE Department LIKE '%Biomed%';

Write only one SQLite query that would answer the user's question. No preamble.
"""

# Initialize memory
memory = ConversationBufferMemory(return_messages=True)

# Updated prompt with memory
memory_prompt = ChatPromptTemplate.from_messages([
    ("system", "Convert questions to SQL using schema: {schema}"),
    MessagesPlaceholder(variable_name="history"),
    ("human", "{question}"),
])

# Memory-enabled query chain
def save_context(input_output):
    """Save conversation context"""
    output = {"output": input_output.pop("output")}
    memory.save_context(input_output, output)
    return output["output"]

sql_chain_with_memory = (
    RunnablePassthrough.assign(
        schema=get_schema,
        history=lambda x: memory.load_memory_variables(x)["history"],
    )
    | memory_prompt
    | llm.bind(stop=["\nSQLResult:"])
    | StrOutputParser()
)

# Final chain with memory
sql_memory_chain = RunnablePassthrough.assign(output=sql_chain_with_memory) | save_context

In [ ]:
import uuid
from langchain_core.messages import HumanMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import ChatPromptTemplate, MessagesPlaceholder
from langchain.memory import ConversationBufferMemory
from langchain_core.runnables import RunnablePassthrough
from langgraph.checkpoint.memory import MemorySaver
from langgraph.graph import START, MessagesState, StateGraph

# SQL generation prompt
system_prompt = """ 
You are a SQLite expert. Given an input question, create one syntactically correct SQLite query to run. Generate only one query. No pre-amble.

Here is the relevant table information:
schema: {schema}
Departments: 'Applied Math & Statistics', 'ART', 'Biomedical Science (BMS)', 'Computer Science (CS), Computer Networks and Cybersecurity (CNCS)', 'Data Science (DS)', 'Dance', 'General Education (GE)'
New/Repeat: Have no values (Don't use New/Repeat in queries)

Tips:
- Use LIKE instead of = in the queries

Below are a number of examples of questions and their corresponding SQL queries.

example 1:
Question:List all departments.
SQL query:SELECT Department FROM Spring_2025_courses;

example 2:
Question:Find all classes that are taught by Dr. Qu.
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Instructor LIKE '%Qu%';

example 3:
Question:List all courses in the Data Science department.
SQL query:SELECT CourseCode, CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Data Science%';

example 4:
Question:Find the total number of courses offered for Spring 2025.
SQL query:SELECT COUNT(CourseCode) FROM Spring_2025_courses;

example 5:
Question:List all professors from Biomed Department.
SQL query:SELECT Instructor FROM Spring_2025_courses WHERE Department LIKE '%Biomed%';

example 6:
Question:Which courses are available in the Biomed department for Spring 2025?
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Biomed%';

example 7:
Question:How many courses are offered under the Arts Management (BFA) program?
SQL query:SELECT COUNT(CourseCode) FROM Spring_2025_courses WHERE Department LIKE Program LIKE '%BFA%'

example 8:
Question:Which courses are available for the Master of Science in Applied Math?
SQL query:SELECT CourseTitle FROM Spring_2025_courses WHERE Program LIKE '%Master of Science%' AND Department LIKE '%Applied Math%';

Write only one SQLite query that would answer the user's question. No pre-amble.
"""

# Define a new graph
workflow = StateGraph(state_schema=MessagesState)

# Memory initialization
memory = ConversationBufferMemory(return_messages=True)

# Define the function that calls the model
def call_model(state: MessagesState):
    response = llm.invoke(state["messages"])
    return {"messages": response}

# Define the two nodes we will cycle between
workflow.add_edge(START, "model")
workflow.add_node("model", call_model)

# Adding memory is straightforward in langgraph
memory_saver = MemorySaver()

app = workflow.compile(checkpointer=memory_saver)

# The thread id is a unique key that identifies this particular conversation.
thread_id = uuid.uuid4()
config = {"configurable": {"thread_id": thread_id}}

# Updated prompt with memory
memory_prompt = ChatPromptTemplate.from_messages([
    ("system", system_prompt),
    MessagesPlaceholder(variable_name="history"),
    ("human", "{question}"),
])

# Memory-enabled query chain
def save_context(input_output):
    """Save conversation context"""
    output = {"output": input_output.pop("output")}
    memory.save_context(input_output, output)
    return output["output"]

sql_chain_with_memory = (
    RunnablePassthrough.assign(
        schema=get_schema,  # Placeholder function to provide schema
        history=lambda x: memory.load_memory_variables(x)["history"],
    )
    | memory_prompt
    | llm.bind(stop=["\nSQLResult:"])
    | StrOutputParser()
)

# Final chain with memory
sql_memory_chain = RunnablePassthrough.assign(output=sql_chain_with_memory) | save_context


In [ ]:
# # Example conversation
# input_message = HumanMessage(content="Which courses are available for the Bachelor of Science in Data Science?")
# for event in app.stream({"messages": [input_message]}, config, stream_mode="values"):
#     event["messages"][-1].pretty_print()

# # Confirming memory functionality
# input_message = HumanMessage(content="Who is teaching the first course on the list?")
# for event in app.stream({"messages": [input_message]}, config, stream_mode="values"):
#     event["messages"][-1].pretty_print()

In [ ]:
def display_query_result(question, include_sql=False):
    """
    Display query results in a formatted way
    
    Args:
        question (str): Natural language question
        include_sql (bool): Whether to show the generated SQL
    """
    # Generate SQL and get response
    sql = sql_generator.invoke({"question": question})
    response = complete_chain.invoke({"question": question})
    
    # Print formatted output
    print("\n" + "="*50)
    print(f"Question: {question}")
    if include_sql:
        print(f"\nGenerated SQL: {sql}")
    print(f"\nAnswer: {response}")
    print("="*50 + "\n")

# Example usage
display_query_result("Which courses are available in the Data Science department for Spring 2025?", include_sql=True)

In [ ]:
# Test the chain
def display_conversation():
    """Display the current conversation history."""
    history = memory.load_memory_variables({})["history"]
    print("\nConversation History:")
    print("=" * 50)
    for msg in history:
        role = "Human" if msg.type == "human" else "Assistant"
        print(f"{role}: {msg.content}\n")


# Test input and output
response1 = sql_memory_chain.invoke({"question": "Which courses are available for the Bachelor of Science in Data Science?"})
print("First Response:", response1)



In [ ]:
response2 = sql_memory_chain.invoke({"question": "Who is teaching the first course on the list?"})
print("Follow-up Response:", response2)

display_conversation()

In [ ]:
def safe_query(question):
    """
    Safely execute a query with error handling
    
    Args:
        question (str): Natural language question
    Returns:
        dict: Result and status
    """
    try:
        response = complete_chain.invoke({"question": question})
        return {
            "success": True,
            "response": response
        }
    except Exception as e:
        return {
            "success": False,
            "error": str(e)
        }

# Example usage
result = safe_query("Which courses are available in the Data Science department for Spring 2025?")
if result["success"]:
    print("Answer:", result["response"])
else:
    print("Error:", result["error"])

In [12]:
import re
from typing import Dict, List

class InputValidator:
    """Input validation and sanitization for database queries"""
    
    # Restricted words that might indicate harmful queries
    RESTRICTED_WORDS = {
        'delete', 'drop', 'truncate', 'update', 'insert', 
        'alter', 'create', 'replace', 'modify', 'grant'
    }
    
    # Allowed table names from our database
    ALLOWED_TABLES = ['spring_2025_courses']  # in lowercase
    
    def __init__(self):
        self.error_messages = []
    
    def validate_question(self, question: str) -> bool:
        """
        Validate a natural language question
        
        Args:
            question (str): User's input question
            
        Returns:
            bool: True if valid, False otherwise
        """
        self.error_messages = []
        
        # Check if question is empty or too long
        if not question or not question.strip():
            self.error_messages.append("Question cannot be empty")
            return False
            
        if len(question) > 500:
            self.error_messages.append("Question is too long (max 500 characters)")
            return False
        
        # Check for basic SQL injection attempts
        question_lower = question.lower()
        if any(word in question_lower for word in self.RESTRICTED_WORDS):
            self.error_messages.append("Question contains restricted keywords")
            return False
        
        # Check for excessive special characters
        if re.search(r'[;{}\\]', question):
            self.error_messages.append("Question contains invalid characters")
            return False
            
        return True
    
    def get_error_messages(self) -> List[str]:
        """Get all error messages from validation"""
        return self.error_messages

In [13]:
class QueryValidator:
    """Validate generated SQL queries before execution"""

    def __init__(self, db_connection):
        self.db = db_connection
        self.error_messages = []
    
    def get_error_messages(self) -> List[str]:
        """Get all error messages from validation"""
        return self.error_messages
    
    def validate_sql(self, sql: str) -> bool:
        """Validate generated SQL query"""
        sql_lower = sql.lower()
        
        # Check if query is read-only (SELECT only)
        if not sql_lower.strip().startswith('select'):
            self.error_messages.append("Only SELECT queries are allowed")
            return False
        
        # Check for multiple statements
        if ';' in sql[:-1]:  # Allow semicolon at the end
            self.error_messages.append("Multiple SQL statements are not allowed")
            return False
        
        # Validate table names
        table = self._extract_table_names(sql_lower)
        if table not in InputValidator.ALLOWED_TABLES:
            self.error_messages.append("Query contains invalid table names")
            return False
            
        return True
    
    def _extract_table_names(self, sql: str) -> str:
        """Extract table names from SQL query"""
        # Simple regex to extract table names
        # Note: This is a basic implementation
        from_matches = re.findall(r'from\s+([a-zA-Z_][a-zA-Z0-9_]*)', sql.lower())
        # join_matches = re.findall(r'join\s+([a-zA-Z_][a-zA-Z0-9_]*)', sql)
        return from_matches[0]

In [14]:
class SafeQueryExecutor:
    """Safe execution of natural language queries"""
    
    def __init__(self, db_connection, llm_chain):
        self.input_validator = InputValidator()
        self.query_validator = QueryValidator(db_connection)
        self.db = db_connection
        self.chain = llm_chain
        
    def execute_safe_query(self, question: str) -> Dict:
        """
        Safely execute a natural language query
        
        Args:
            question (str): User's natural language question
            
        Returns:
            dict: Query result and status
        """
        # Validate input
        if not self.input_validator.validate_question(question):
            return {
                'success': False,
                'error': self.input_validator.get_error_messages(),
                'query': None,
                'result': None
            }
        
        try:
            # Generate SQL query
            sql_query = sql_generator.invoke({"question": question})
            
            # Validate generated SQL
            if not self.query_validator.validate_sql(sql_query):
                return {
                    'success': False,
                    'error': self.query_validator.get_error_messages(),
                    'query': sql_query,
                    'result': None
                }
            
            # Execute query
            result = complete_chain.invoke({"question": question})
            
            return {
                'success': True,
                'error': None,
                'query': sql_query,
                'result': result
            }
            
        except Exception as e:
            return {
                'success': False,
                'error': [str(e)],
                'query': None,
                'result': None
            }

In [ ]:
# Initialize the safe executor
safe_executor = SafeQueryExecutor(db, complete_chain)

result1 = safe_executor.execute_safe_query("Which courses are available in the Data Science department for Spring 2025?")
print("\nValid Query Result:")
print(result1)

In [15]:
# Initialize the safe executor
safe_executor = SafeQueryExecutor(db, complete_chain)

# Example queries
def test_queries():
    # Valid query
    result1 = safe_executor.execute_safe_query("Which courses are available in the Data Science department for Spring 2025?")
    print("\nValid Query Result:")
    print(result1)
    
    # Invalid query with SQL injection attempt
    result2 = safe_executor.execute_safe_query("""What are the details of the course ‘Introduction to Python’?""")
    print("\nInvalid Query Result:")
    print(result2)
    
    # Query with restricted words
    result3 = safe_executor.execute_safe_query("How many courses are offered under the Computer Science (Bachelor of Science) program?")
    print("\nRestricted Query Result:")
    print(result3)

    # Query with restricted words
    result4 = safe_executor.execute_safe_query("Show me the courses taught by Dr. Qu in Spring 2025.")
    print("\nRestricted Query Result:")
    print(result4)
    
# Run test queries
test_queries()


Valid Query Result:
{'success': True, 'error': None, 'query': " \nSELECT CourseTitle FROM Spring_2025_courses WHERE Department LIKE '%Data Science%';", 'result': ' The available courses in the Data Science department for Spring 2025 are Introduction to Data Science, Career Development in Data Science, Data Structures, Data Visualization, Data Inference, Data Mining, Big Data Engineering, Independent Study for Data Science, Senior Project, Mathematical Foundation for Data Science, Computational Foundation for Data Science, Probability for Data Science, Exploratory Data Analysis and Visualization, Modern Applied Statistical Learning, Data Mining for Business, Big Data and Data Engineering, Design and Analysis of Experiments, and Capstone Project.'}

Invalid Query Result:
{'success': True, 'error': None, 'query': " \nSELECT * FROM Spring_2025_courses WHERE CourseTitle LIKE '%Introduction to Python%';", 'result': '  The course Introduction to Python is not offered in Spring 2025.'}

Restr

In [ ]:
result1 = safe_executor.execute_safe_query("DROP TABLE courses;")
result1